# Explicit ForAll

> Juan Pablo Yamamoto  
> jpyamamoto\[at\]ciencias.unam.mx  
> Lógica Computacional II. Semestre 2025-1.

## Polimorfismo en tipos

Haskell está construido sobre el fundamento del Sistema F.
- Bajo la correspondencia "proposiciones como tipos" tenemos lógica de Segundo Orden.
- Polimorfismo sobre tipos.

### `ExplicitForAll`

En Haskell, el cuantificador universal tiende a estar oculto, pero ímplicito.

In [1]:
id :: a -> a
id x = x

In [2]:
:t id

id :: forall a. a -> a

In [3]:
fst :: (a, b) -> a
fst (x, _) = x

In [4]:
:t fst

fst :: forall a b. (a, b) -> a

Pero también podemos pedirle al compilador que nos permita escribir explícitamente los cuantificadores:

In [5]:
{-# LANGUAGE ExplicitForAll #-}

In [6]:
id' :: forall a . a -> a
id' x = x

In [7]:
:t id'

id' :: forall a. a -> a

In [8]:
fst' :: forall a b . (a, b) -> a
fst' (x, _) = x

In [9]:
:t fst'

fst' :: forall a b. (a, b) -> a

### `ScopedTypeVariables`

Debido a que en general no damos todos los tipos de todos los términos de un programa, puede resultar difícil para Haskell inferir correctamente el tipificado correcto en todos los casos. De hecho, es demostrable que en los sistemas al estilo Church, la inferencia de tipos es no decidible.

Debido a ello, hay problemas al tipificar fragmentos como el siguiente:

In [10]:
import Data.List

In [12]:
weirdList :: Ord a => [a] -> [(a, a)]
weirdList xs = zip sortedList nubbedList
    where sortedList :: [a]
          sortedList = sort xs
          nubbedList :: [a]
          nubbedList = nub xs

: 

In [13]:
{-# LANGUAGE ScopedTypeVariables #-}

In [15]:
weirdList :: forall a . Ord a => [a] -> [(a, a)]
weirdList xs = zip sortedList nubbedList
    where sortedList :: [a]
          sortedList = sort xs
          nubbedList :: [a]
          nubbedList = nub xs

### `LiberalTypeSynonyms`

En algunas ocasiones, puede resultar de utilidad expandir las definiciones de los alias de tipos, previo a realizar el análisis estático.

In [16]:
type Foo a = a -> a -> Bool
 
-- (forall b . b -> b) -> (forall b . b -> b) -> Bool
f :: Foo (forall b . b -> b)
f _ _ = True

: 

In [17]:
{-# LANGUAGE LiberalTypeSynonyms #-}

In [18]:
type DropTwoBool a = a -> a -> Bool
 
ignore :: DropTwoBool (forall b. b->b)
ignore _ _ = True

In [19]:
:t ignore

ignore :: DropTwoBool (forall b. b -> b)

### `RankNTypes`

Anteriormente hicimos trampa. Haskell por defecto activa esta extensión.

¿Qué sucede si la desactivamos?

In [20]:
{-# LANGUAGE NoRankNTypes #-}

In [21]:
f :: (forall b . b -> b) -> (forall b . b -> b) -> Bool
f _ _ = True

: 

Entendemos el `rank` de un tipo como:
- Si el tipo no tiene variables de tipo, es rank 0.
- Si el tipo tiene cuantificación universal, pero los cuantificadores nunca están a la izquierda de una flecha, son rango 1.
- Si el tipo tiene un cuantificador de rank `n` a la izquierda de una flecha, es de rank `n+1`.

In [22]:
{-# LANGUAGE RankNTypes #-}

In [25]:
transformAnyType :: (forall a. a -> a) -> b -> b
transformAnyType f x = f x

Line 2: Eta reduce
Found:
transformAnyType f x = f x
Why not:
transformAnyType f = f

In [27]:
printAnyTransf :: (forall a. Show a => a -> a) -> String -> Int -> String
printAnyTransf g prefix suffix = g prefix ++ show (g suffix)

In [28]:
printAnyTransf id "key" 10

"key10"

### `ImpredicativeTypes`

In [29]:
f :: [forall a. a -> a]
f = [id]

: 

In [30]:
g :: Maybe (forall a . a -> a)
g = Just id

: 

In [31]:
{-# LANGUAGE ImpredicativeTypes #-}

In [32]:
f :: [forall a. a -> a]
f = [id]

In [33]:
g :: Maybe (forall a . a -> a)
g = Just id

In [34]:
{-# LANGUAGE NoImpredicativeTypes #-}

In [36]:
h :: forall a . Maybe (a -> a)
h = Just id